In [ ]:
!pip install pyspark
!pip install geoviews
!pip install datashader

import pyspark
import pickle
import pyspark.sql.functions as F
import pyspark.sql.types as T
import geoviews as gv
import colorcet as cc
import holoviews as hv
import datashader as ds
import matplotlib as mpl
import geoviews.tile_sources as gts
import datashader.transfer_functions as tf

from google.colab import drive
from pyspark.sql.functions import col
from pyspark.sql.functions import size
from pyspark.sql import SparkSession
from pyspark.sql.types import IntegerType, FloatType, StringType, StructType
from pyspark.sql import Window
from geopy.distance import geodesic
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.cluster import KMeans
from sklearn.mixture import GaussianMixture

from typing import Optional
from holoviews.operation.datashader import datashade
from holoviews import opts
from IPython.display import IFrame
from IPython.core.display import display
from bokeh.plotting import show, output_notebook

In [37]:
# tworzenie sesji w Sparku
spark = SparkSession.builder.appName('SparkWindows').getOrCreate()

In [38]:
# wczytanie danych z google drive
drive.mount('/content/drive')

columns = ['lon', 'lat', 'Date', 'Rainf', 'Evap', 'AvgSurfT', 'Albedo','SoilT_10_40cm', 'GVEG', 'PotEvap', 'RootMoist', 'SoilM_100_200cm']

# Utworzenie schematu okreslajacego typ zmiennych
schema = StructType()
for i in columns:
  if i == "Date":
    schema = schema.add(i, IntegerType(), True)
  else:
    schema = schema.add(i, FloatType(), True)

nasa = spark.read.format('csv').option("header", True).schema(schema).load('/content/drive/MyDrive/BigMess/NASA/NASA.csv')
nasa.createOrReplaceTempView("nasa")
nasa.show(5)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
+---------+-------+------+-----+---------+---------+---------+-------------+----------+---------+----------+---------------+
|      lon|    lat|  Date|Rainf|     Evap| AvgSurfT|   Albedo|SoilT_10_40cm|      GVEG|  PotEvap| RootMoist|SoilM_100_200cm|
+---------+-------+------+-----+---------+---------+---------+-------------+----------+---------+----------+---------------+
|-112.0625|25.0625|200001|  0.0|   4.3807| 288.0707| 41.47715|    289.00714|0.19712792|139.13737|  243.2525|      108.76931|
|-111.9375|25.0625|200001|  0.0|4.6673994|287.39276|41.509407|     288.8017|0.19860405|162.25638| 220.77466|       90.67495|
|-111.8125|25.0625|200001|  0.0|5.8487973| 287.6554|41.505375|    289.55984|0.17118543|121.55404| 103.95005|      161.94794|
|-111.6875|25.0625|200001|  0.0|6.4366016| 287.5386|41.501343|    289.61142|0.17118543|127.63407|106.032845|      163.444

In [39]:
nasa_ym = spark.sql("""
          SELECT
          CAST(SUBSTRING(CAST(Date AS STRING), 1, 4) AS INT) AS Year,
          CAST(SUBSTRING(CAST(Date AS STRING), 5, 2) AS INT) AS Month,
          n.*
          FROM nasa n
          """)
nasa_ym = nasa_ym.drop("Date")

nasa_ym.createOrReplaceTempView("nasa_ym")

In [40]:
# wybieramy dane z lipca 2k23
SparkDataFrame_2023_7 = nasa_ym.filter('Year = 2023').filter('Month = 07')
SparkDataFrame_2023_7.show(5)

+----+-----+---------+-------+------+---------+--------+--------+-------------+-----------+--------+---------+---------------+
|Year|Month|      lon|    lat| Rainf|     Evap|AvgSurfT|  Albedo|SoilT_10_40cm|       GVEG| PotEvap|RootMoist|SoilM_100_200cm|
+----+-----+---------+-------+------+---------+--------+--------+-------------+-----------+--------+---------+---------------+
|2023|    7|-112.0625|25.0625|0.4906| 2.114799|298.2533|39.52822|     294.8851|0.002595433|278.5755| 351.1361|       185.8745|
|2023|    7|-111.9375|25.0625|0.4506|   1.5034|299.8121|39.59543|     296.4973|0.002595433|368.6648| 328.9924|       171.5948|
|2023|    7|-111.8125|25.0625|0.4106| 1.010101|302.5172|39.59409|     298.7112|        0.0|312.8552| 146.7265|       199.5868|
|2023|    7|-111.6875|25.0625|0.3749|0.9301001|303.3653|39.59543|     299.5569|        0.0|328.7048| 143.9877|       198.7378|
|2023|    7|-111.5625|25.0625|0.4388|0.9732001|302.8797|39.60215|     299.3457|        0.0|434.0797| 189.9473| 

In [42]:
# konwertujemy do Pandasa
pd_2023_07 = SparkDataFrame_2023_7.toPandas()
pd_2023_07 = pd_2023_07.drop(columns = ['Year', 'Month'])

In [289]:
# wczytanie zbioru anotowanego
NASA_sample_an = pd.read_csv('/content/drive/MyDrive/BigMess/NASA/NASA_an.csv',sep=';')
NASA_sample_an['pustynia_i_step'] = NASA_sample_an.pustynia + NASA_sample_an.step
NASA_sample_an["pustynia_i_step"] = NASA_sample_an["pustynia_i_step"].apply(lambda x: 0 if x==1 else 1)

## Funkcje do liczenia średniej wartości zmiennych w okolicy punktu

In [43]:
def create_lon_lat_pairs(df: pd.DataFrame, tolerance_lon: float = 5, tolerance_lat: float = 5, verbose: bool = False):
    projection = df[['lon', 'lat']]
    result = {}
    if verbose:
        count = 0
    for row in projection.itertuples(index=True):
        index, lon, lat = row.Index, row.lon, row.lat
        if verbose:
            count += 1
            print(f'Processing item no {count}')
        result[(lon, lat)] = set()
        for lon_other, lat_other in result:
            if (abs(lon - lon_other) < tolerance_lon) and (abs(lat - lat_other) < tolerance_lat):
                result[(lon, lat)].add((lon_other, lat_other))
                result[(lon_other, lat_other)].add((lon, lat))

    def generator():
        for key, values in result.items():
            lon, lat = key
            for value in values:
                lon_other, lat_other = value
                yield lon, lat, lon_other, lat_other

    columns = ['lon', 'lat', 'lon_other', 'lat_other']
    return pd.DataFrame(generator(), columns=columns)


In [ ]:
def haversine_distance(lon1, lat1, lon2, lat2):
    """
    Calculate the Haversine distance between two points specified by their longitude and latitude.

    Parameters:
    lon1, lat1: Longitude and latitude of the first point
    lon2, lat2: Longitude and latitude of the second point

    Returns:
    Haversine distance in kilometers
    """
    R = 6371  # Earth radius in kilometers

    # Convert degrees to radians
    lon1, lat1, lon2, lat2 = map(np.radians, [lon1, lat1, lon2, lat2])

    # Haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = np.sin(dlat / 2) ** 2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2) ** 2
    c = 2 * np.arcsin(np.sqrt(a))

    # Calculate distance
    distance = R * c
    return distance

In [ ]:
def average_over_space_window(df: pd.DataFrame,max_distance: float, df_grid: Optional[pd.DataFrame] = None, tolerance_lon : float =1, tolerance_lat: float =1) -> pd.DataFrame:
  """
  some parameters works only id df_grid is left None
  df grid must also have proper column names
  """
  if df_grid is None:
    df_grid = create_lon_lat_pairs(df, tolerance_lon=tolerance_lon, tolerance_lat=tolerance_lat)
    df_grid['distance'] = haversine_distance(df_grid['lon'], df_grid['lat'], df_grid['lon_other'], df_grid['lat_other'])
  df_grid = df_grid[df_grid['distance'] < max_distance]
  df_grid = df_grid.drop(columns='distance')
  window_data = pd.merge(df_grid, df, left_on = ['lon_other', 'lat_other'], right_on = ['lon', 'lat'])
  window_data.rename(columns={'lon_x': 'lon', 'lat_x': 'lat'}, inplace=True)
  window_data.drop(['lon_other', 'lat_other', 'lon_y', 'lat_y'], axis=1, inplace=True)
  return window_data.groupby(['lon', 'lat']).mean().reset_index()



## Funkcje do EM i k-średnich

In [ ]:
def MinMaxScaling(df: pd.DataFrame, attributes: list) -> pd.DataFrame:
  """
  Funkcja służąca do przeskalowania wybranych atrybutów za pomocą funkcji MinMaxScaler, a następnie stworzenia nowej ramki danych z tylko przeskalowanymi atrybutami.
  Parametry:
  - df (DataFrame): Pandas DataFrame zawierająca co najmniej atrybuty,
  - attributes (str): atrybuty, które będziemy skalować.
  """
  scaled_data = MinMaxScaler().fit_transform(df[attributes])
  scaled_df = pd.DataFrame(scaled_data, columns=attributes)
  return scaled_df

In [ ]:
def do_kmeans_and_return_df_with_cluster_column(df: pd.DataFrame, scaled_df: pd.DataFrame, n_clusters: int, random_state: int) -> pd.DataFrame:
  """
  Funkcja wykonuje grupowanie k-średnich dla n_clusters klastrów oraz tworzy nową kolumnę z predykcjami algorytmu k-średnich w ramce danych df.
  Parametry:
  - df (DataFrame): Pandas DataFrame zawierająca co najmniej te same kolumny co scaled_df,
  - scaled_df (DataFrame): Pandas DataFrame zawierająca przeskalowane kolumny, na podstawie których dokonywane jest grupowanie,
  - n_clusters (int): maksymalna liczba klastrów,
  - random_state (int): ziarno losowości.
  """
  kmeans = KMeans(n_clusters = n_clusters, init='k-means++', random_state=random_state)
  kmeans.fit(scaled_df)
  pred = kmeans.predict(scaled_df)
  df['cluster'] = pred
  return df

In [245]:
def do_EM_and_return_df_with_cluster_column(df: pd.DataFrame, scaled_df: pd.DataFrame, n_clusters: int, random_state: int) -> pd.DataFrame:
  """
  Funkcja wykonuje grupowani EM dla n_clusters klastrow oraz tworzy nową kolumnę z predykcjami algorytmu EM w ramce danych df.
  Parametry:
  - df (DataFrame): Pandas DataFrame zawierająca co najmniej te same kolumny co scaled_df,
  - scaled_df (DataFrame): Pandas DataFrame zawierająca przeskalowane kolumny, na podstawie których dokonywane jest grupowanie,
  - n_clusters (int): maksymalna liczba klastrow,
  - random_state (int): ziarno losowosci.
  """
  gm = GaussianMixture(n_components = n_clusters, n_init = 200, max_iter=200, init_params= 'random_from_data', covariance_type='spherical', random_state=random_state)
  gm_result = gm.fit_predict(scaled_df)
  new_df = df.copy()
  new_df['cluster'] = gm_result
  return new_df

## Funkcje do map

In [ ]:
'''
Funkcja jako argumenty bierze listę wartości określających granice przedziałów liczbowych, które
będą określać jak dla rozważanego parametru mają zmieniać się kolory punktów, których lista stanowi
drugi argument funkcji.
'''
def get_colormap(values: list, colors_palette: list, name = 'custom'):
    values = np.sort(np.array(values))
    values = np.interp(values, (values.min(), values.max()), (0, 1))
    cmap = mpl.colors.LinearSegmentedColormap.from_list(name, list(zip(values, colors_palette)))
    return cmap

In [ ]:
def plot_map(df: pd.DataFrame, parameter_name: str, colormap: mpl.colors.LinearSegmentedColormap, title: str,
             point_size: int = 8, width: int = 800, height: int = 500, alpha: float = 1,
             bgcolor: str = 'white', colorbar_verbose: bool = True):

    gdf = gv.Points(df, ['lon', 'lat'], [parameter_name]) # obiekt zawierający punkty
    tiles = gts.OSM # wybór mapy tła, w tym wypadku OpenStreetMap

    # łączenie mapy tła z punktami i ustawienie wybranych parametrów wizualizacji
    map_with_points = tiles * gdf.opts(
        title=title,
        color=parameter_name,
        cmap=colormap,
        size=point_size,
        width=width,
        height=height,
        colorbar=colorbar_verbose,
        toolbar='above',
        tools=['hover', 'wheel_zoom', 'reset'],
        alpha=alpha, # przezroczystość
        bgcolor=bgcolor
    )

    return hv.render(map_with_points)

In [93]:
display(IFrame("https://www.google.com/maps/embed?pb=!1m14!1m12!1m3!1d13982681.959428234!2d-98.66341902257437!3d38.39997874427714!2m3!1f0!2f0!3f0!3m2!1i1024!2i768!4f13.1!5e1!3m2!1spl!2spl!4v1703000232420!5m2!1spl!2spl", '800px', '500px'))

## Przygotowanie danych do modeli. Policzenie średnich wartości zmiennych w promieńu 50km od punktu.


In [ ]:
# tworzymy mozliwe pary wspolrzednych
df_grid = create_lon_lat_pairs(pd_2023_07, tolerance_lon=1, tolerance_lat=1, verbose = True)
df_grid.head()

In [46]:
# liczymy odleglosci
df_grid['distance'] = haversine_distance(df_grid['lon'], df_grid['lat'], df_grid['lon_other'], df_grid['lat_other'])
df_grid.sample(5)

lon      lat  lon_other  lat_other    distance
7018325   -86.4375  40.0625   -86.5625    39.3125   84.079289
11621327 -118.4375  46.6875  -118.1875    45.8125   99.176237
14431215  -84.9375  50.4375   -85.8125    49.5625  115.660196
4547837  -107.1875  36.4375  -106.8125    36.0625   53.567792
4519860   -77.4375  36.3125   -78.1875    36.1875   68.675476

In [47]:
df_grid[['lon', 'lat']].duplicated()

0           False
1            True
2            True
3            True
4            True
            ...  
16180206     True
16180207     True
16180208     True
16180209     True
16180210     True
Length: 16180211, dtype: bool

In [145]:
# wybieramy te ktore nie przekraczaja 50 jednostek
df_grid = df_grid[df_grid['distance'] < 50]

In [251]:
# zastepujemy wartosci pomiarowe wartosciami srednimi z okolicy punktu o srednicy 50km
result = average_over_space_window(pd_2023_07,max_distance=50, df_grid=df_grid)
result

lon      lat       Rainf       Evap    AvgSurfT     Albedo  \
0     -124.9375  48.8125   46.378132  43.351696  287.454407  19.672167   
1     -124.9375  48.9375   38.703762  45.637558  288.086945  19.562140   
2     -124.9375  49.0625   31.283787  46.819729  288.391510  19.465055   
3     -124.9375  49.1875   25.374254  46.117237  288.778107  19.402172   
4     -124.9375  49.3125   24.066866  48.745388  289.631226  19.381721   
...         ...      ...         ...        ...         ...        ...   
76058  -67.0625  52.4375  188.332336  76.357849  291.355957  20.007141   
76059  -67.0625  52.5625  189.133011  75.393684  291.221863  20.211525   
76060  -67.0625  52.6875  186.674088  73.517464  291.090759  20.397764   
76061  -67.0625  52.8125  184.807098  71.806664  290.996826  20.522945   
76062  -67.0625  52.9375  181.394714  70.537338  290.932312  20.601208   

       SoilT_10_40cm      GVEG     PotEvap   RootMoist  SoilM_100_200cm  
0         283.653290  0.855547  221.358536  434.243927       220.350677  
1         284.136261  0.864783  238.032196  419.038879       213.716385  
2         284.368530  0.870183  245.850021  405.951233       208.583176  
3         284.582611  0.869504  250.105255  398.881989       206.352814  
4         285.285400  0.865932  251.896332  397.771637       205.774796  
...              ...       ...         ...         ...              ...  
76058     281.777863  0.587589  215.546951  481.073486       279.629791  
76059     281.483307  0.594050  214.624954  518.436523       282.176086  
76060     281.232422  0.594975  211.269760  520.450989       284.878998  
76061     281.060852  0.592041  208.493454  520.240845       287.256012  
76062     280.951599  0.589899  205.899536  513.106628       288.658386  

[76063 rows x 11 columns]

# Najlepsze modele na danych uśrednionych z okolicy o średnicy 50km

K-średnich

In [264]:
scaled_pd_2023_7 = MinMaxScaling(result, ['Rainf','Evap' ,'AvgSurfT', 'Albedo', 'SoilT_10_40cm', 'GVEG', 'PotEvap', 'RootMoist', 'SoilM_100_200cm'])
output_pd_2023_7 = do_kmeans_and_return_df_with_cluster_column(result, scaled_pd_2023_7, 2, 123)

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(


In [265]:
colormap_cluster = get_colormap([0, 1], ['yellow', 'darkgreen'])
output_notebook()
show(plot_map(df=output_pd_2023_7, parameter_name='cluster', colormap=colormap_cluster, title="K_średnich - lipiec 2023", alpha=1))

/usr/local/lib/python3.10/dist-packages/holoviews/core/util.py:1585: PanelDeprecationWarning: 'param_value_if_widget' is deprecated and will be removed in version 1.4, use 'transform_reference' instead.
  value = param_value_if_widget(value)


In [266]:
output_with_anotated = output_pd_2023_7.merge(NASA_sample_an, left_on=['lon','lat'], right_on = ['lon','lat'], how='inner')

In [267]:
positive = len(output_with_anotated.loc[output_with_anotated.cluster == output_with_anotated.pustynia_i_step])
accuracy = str(round(positive/len(NASA_sample_an)*100,2))
print("Accuracy na poziomie",accuracy+"%.")

Accuracy na poziomie 85.86%.


## LightGBM

In [274]:
# przetestujemy jak na naszych danych sprawdzi sie LightGBM
model_lgbm_m2_7_path='/content/drive/MyDrive/BigMess/NASA/Modele/Klasyfikacja/LightGBM/lgbm_m2_7'
with open(model_lgbm_m2_7_path , 'rb') as f:
    model_LGBM = pickle.load(f)

In [277]:
result = result.drop(columns = ['cluster'])
result_no_lonlat = result.drop(columns = ['lon', 'lat'])
LGBM_predict_2023_07 = model_LGBM.predict(result_no_lonlat)
result['Prediction'] = LGBM_predict_2023_07

In [278]:
colormap_cluster = get_colormap([0, max(result.Prediction.values)], ['darkgreen', 'yellow'])
output_notebook()
show(plot_map(df=result, parameter_name='Prediction', colormap=colormap_cluster, title="LightGBM - Lipiec 2023", alpha=0.5))

/usr/local/lib/python3.10/dist-packages/holoviews/core/util.py:1585: PanelDeprecationWarning: 'param_value_if_widget' is deprecated and will be removed in version 1.4, use 'transform_reference' instead.
  value = param_value_if_widget(value)


In [279]:
output_with_anotated = result.merge(NASA_sample_an, left_on=['lon','lat'], right_on = ['lon','lat'], how='inner')
positive = len(output_with_anotated.loc[output_with_anotated.Prediction == output_with_anotated.pustynia_i_step])
accuracy = str(round(positive/len(NASA_sample_an)*100,2))
print("Accuracy na poziomie",accuracy+"%.")

Accuracy na poziomie 85.61%.


## Lasy

In [280]:
# teraz zobaczymy jak poradzą sobie lasy z naszymi danymi
model_las_m2_7_path='/content/drive/MyDrive/BigMess/NASA/Modele/Klasyfikacja/Lasy/las_m2_7'
with open(model_m3_path , 'rb') as f:
    model_forest = pickle.load(f)

In [282]:
result = result.drop(columns = ['AvgSurfT', 'Evap', 'PotEvap', 'Prediction'])
result_no_lonlat = result.drop(columns = ['lon', 'lat'])
forest_predict_2023_07 = model_forest.predict(result_no_lonlat)
result['Prediction'] = forest_predict_2023_07

In [283]:
colormap_cluster = get_colormap([0, max(result.Prediction.values)], ['darkgreen', 'yellow'])
output_notebook()
show(plot_map(df=result, parameter_name='Prediction', colormap=colormap_cluster, title="Lasy - Lipiec 2023", alpha=0.5))

/usr/local/lib/python3.10/dist-packages/holoviews/core/util.py:1585: PanelDeprecationWarning: 'param_value_if_widget' is deprecated and will be removed in version 1.4, use 'transform_reference' instead.
  value = param_value_if_widget(value)


jak widzimy lasy nie za dobrze radzą sobie z naszymi danymi

## EM

In [290]:
output_EM = do_EM_and_return_df_with_cluster_column(result, scaled_pd_2023_7, 2, 123)

In [291]:
colormap_cluster = get_colormap([0, max(output_EM.cluster.values)], ['yellow', 'darkgreen'])
output_notebook()
show(plot_map(df=output_EM, parameter_name='cluster', colormap=colormap_cluster, title="EM - Lipiec 2023", alpha=1))

/usr/local/lib/python3.10/dist-packages/holoviews/core/util.py:1585: PanelDeprecationWarning: 'param_value_if_widget' is deprecated and will be removed in version 1.4, use 'transform_reference' instead.
  value = param_value_if_widget(value)


In [292]:
output_with_anotated = output_EM.merge(NASA_sample_an, left_on=['lon','lat'], right_on = ['lon','lat'], how='inner')
positive = len(output_with_anotated.loc[output_with_anotated.cluster == output_with_anotated.pustynia_i_step])
accuracy = str(round(positive/len(NASA_sample_an)*100,2))
print("Accuracy na poziomie",accuracy+"%.")

Accuracy na poziomie 87.11%.
